In [156]:
# Stock Downloader Yahoo In-Memory / Python 3
def YahooStocks(tickers = ["MSFT", "FB"], freq = "d", selectColumn = "AdjClose", fromDate = None, toDate = None):
    
    """
    NOTES:
    tickers = Defaults to ["MSFT","FB"], and uses a list as input
    freq = Defaults to "d" (Note: Can be "d"[daily],"m"[monthly],"q"[quarterly], or "v"[dividends])
    selectColumn = Defaults to "AdjClose". Can choose between "Open", "High", "Low", "Close", "Volume" or "AdjClose".
    fromDate: Defaults to 1yr lag. Must include YYYY/MM/DD or YYYY-MM-DD string as format.
    toDate: Defaults to 1yr lag. Must include YYYY/MM/DD or YYYY-MM-DD string as format.
    
    """
    import pandas as pd
    import datetime
    # For downloader
    import urllib.request
    import io
    import urllib.error
    
    stackData = pd.DataFrame()
    fullData = pd.DataFrame()
    fullDataClean = pd.DataFrame()
    
    for ticker in tickers:
        
        data = pd.DataFrame() 
        fromDateInternal = pd.DataFrame() 
        toDateInternal = pd.DataFrame()
        tickersNarrow = pd.DataFrame()

        url = []
        xld = []
        xlds = []


        if fromDate is None:

            toDateInternal = datetime.datetime.now()
            fromDateInternal = toDateInternal - datetime.timedelta(days=360)

            toDateInternal  = str(toDateInternal.date())
            toDateInternal = toDateInternal.replace('-', '/')
            toDateInternal = pd.to_datetime(toDateInternal, format = "%Y/%m/%d").date()


            fromDateInternal  = str(fromDateInternal.date())
            fromDateInternal = fromDateInternal.replace('-', '/')
            fromDateInternal = pd.to_datetime(fromDateInternal, format = "%Y/%m/%d").date()

        else:
            

            fromDateInternal = fromDate
            fromDateInternal = fromDateInternal.replace('-', '/')
            fromDateInternal = datetime.datetime.strptime(fromDateInternal, "%Y/%m/%d").date()


            if toDate == None: 
                toDateInternal = str(datetime.datetime.now().date())
                toDateInternal = toDateInternal.replace('-', '/')
                toDateInternal = datetime.datetime.strptime(toDateInternal, "%Y/%m/%d").date()

            else:
                toDateInternal  = str(toDate)
                toDateInternal = toDateInternal.replace('-', '/')
                toDateInternal = datetime.datetime.strptime(toDateInternal, "%Y/%m/%d").date()

        #print(fromDateInternal)
        #print(toDateInternal)
        
        # Downloader
        url = "http://real-chart.finance.yahoo.com/table.csv?s=" + ticker + "&a=0" + str(fromDateInternal.month) + "&b=" + \
            str(fromDateInternal.day) + "&c=" + str(fromDateInternal.year) + "&d=0" + str(toDateInternal.month) + "&e="  +  \
                str(toDateInternal.day) + "&f=" +  str(toDateInternal.year) + "&g=" + freq + "&ignore=.csv"

        #Checks if 404 error from no data in ticker
        try:
            
            xld = urllib.request.urlopen(url).read()
            xld = xld.decode('utf-8')
            xlds = io.StringIO(xld)
            data = pd.read_csv(xlds, delimiter=',', header=None, skiprows=1)
            data.columns = ["Date", "Open", "High", "Low", "Close", "Volume", "AdjClose"]

            data['Date'] = pd.to_datetime(data['Date'], format = "%Y-%m-%d")
            data[["Open", "High", "Low", "Close", "Volume", "AdjClose"]] = data[["Open", "High", "Low", "Close", "Volume", "AdjClose"]].astype(float)
            data["Security"] = ticker

            stackData = pd.concat([stackData, data])
            
            print(ticker, ": ", url)

            
        except urllib.error.HTTPError as err:
            print(ticker, ": No data for ticker exists in the given date range")
            if err.code == 404:
                continue
            else:
                raise
                
    ## Find all dates and create index
    # Returns all dates among used ticker data
    uniqueDates = stackData.Date.map(lambda t: t.date()).unique()
    uniqueDates = pd.DataFrame(uniqueDates, columns = ['Date'] ).sort_values(by = "Date", ascending = [0])
    uniqueDates['Date'] = pd.to_datetime(uniqueDates['Date'], format = "%Y-%m-%d")

    fullData = uniqueDates
    
    tickersNarrow = stackData.Security.unique() # Find usable tickers
    
    ## Loop through each ticker
    for ticker in tickersNarrow:
        fullData = pd.merge(fullData, stackData[stackData.Security==ticker][['Date',selectColumn]], on = "Date", how = 'left')
        fullData.rename(columns={selectColumn:(ticker + "_" + selectColumn)}, inplace = True)
        
        
    # Drop any rows with NaN
    fullDataClean = fullData.dropna()
    
    print()
    print( "fullData Dates range from: ", min(fullData.Date).date(), " to ", max(fullData.Date).date() )
    print( "fullDataClean Dates range from: ", min(fullDataClean.Date).date(), " to ", max(fullDataClean.Date).date() )
    print()

    return fullData, fullDataClean, stackData


#     tickers = Defaults to ["MSFT","FB"], and uses a list as input
#     freq = Defaults to "d" (Note: Can be "d"[daily],"m"[monthly],"q"[quarterly], or "v"[dividends])
#     selectColumn = Defaults to "AdjClose". Can choose between "Open", "High", "Low", "Close", "Volume" or "AdjClose".
#     fromDate: Defaults to 1yr lag. Must include YYYY/MM/DD or YYYY-MM-DD string as format.
#     toDate: Defaults to 1yr lag. Must include YYYY/MM/DD or YYYY-MM-DD string as format.

tickers = ['GOOG','C',"F", "MSFT"]
fullData, fullDataClean, stackData = YahooStocks(tickers, freq = "w", selectColumn = "Open", fromDate = "1990/01/01", toDate = "2000/01/01")
fullDataClean 

GOOG : No data for ticker exists in the given date range
C :  http://real-chart.finance.yahoo.com/table.csv?s=C&a=01&b=1&c=1990&d=01&e=1&f=2000&g=w&ignore=.csv
F :  http://real-chart.finance.yahoo.com/table.csv?s=F&a=01&b=1&c=1990&d=01&e=1&f=2000&g=w&ignore=.csv
MSFT :  http://real-chart.finance.yahoo.com/table.csv?s=MSFT&a=01&b=1&c=1990&d=01&e=1&f=2000&g=w&ignore=.csv

fullData Dates range from:  1990-02-01  to  2000-01-31
fullDataClean Dates range from:  1990-02-01  to  2000-01-31



Date     C_Open     F_Open   MSFT_Open
0   2000-01-31  56.623585  49.812538   97.625000
1   2000-01-24  56.998577  51.812542  103.796883
2   2000-01-18  58.061050  53.750038  111.812500
3   2000-01-10  54.936127  54.750034  113.437500
4   2000-01-03  55.623611  52.750031  117.375000
5   1999-12-27  56.061100  53.000038  118.437500
6   1999-12-20  54.498638  49.812538  114.812500
7   1999-12-13  55.998600  49.000027   93.609383
8   1999-12-06  56.936077  52.437534   95.250000
9   1999-11-29  54.186146  50.437531   90.125000
10  1999-11-22  55.561111  50.625031   89.625000
11  1999-11-15  55.123623  53.375038   88.250000
12  1999-11-08  53.873653  53.312531   84.812500
13  1999-11-01  53.748657  55.000042   93.250000
14  1999-10-25  47.748806  53.562538   92.000000
15  1999-10-18  42.623936  50.625031   87.187500
16  1999-10-11  46.498837  52.750031   94.625000
17  1999-10-04  43.436417  50.875038   90.500000
18  1999-09-27  44.498890  49.875027   92.000000
19  1999-09-20  43.748905  50.062527   96.000000
20  1999-09-13  43.061424  50.750023   94.500000
21  1999-09-07  45.686359  52.625034   94.875000
22  1999-08-30  47.373817  51.375034   92.875000
23  1999-08-23  47.498814  51.312527   84.312500
24  1999-08-16  45.748856  48.312531   85.062500
25  1999-08-09  42.123947  48.187538   85.625000
26  1999-08-02  44.936378  49.625038   85.687500
27  1999-07-26  47.248821  53.000038   88.875000
28  1999-07-19  49.936253  54.500042  100.000000
29  1999-07-12  49.248768  55.875034   93.187500
..         ...        ...        ...         ...
493 1990-08-20  29.124998  36.249943   60.250320
494 1990-08-13  30.125006  37.749977   63.750240
495 1990-08-06  30.500006  38.749992   61.500240
496 1990-07-30  31.749998  41.374992   68.500084
497 1990-07-23  33.500004  43.124969   73.249916
498 1990-07-16  36.750000  44.499939   78.750000
499 1990-07-09  35.375004  43.999989   73.499763
500 1990-07-02  34.250004  43.874985   76.000320
501 1990-06-25  33.999996  44.374939   75.625198
502 1990-06-18  33.500004  45.624966   75.749763
503 1990-06-11  31.749998  45.874973   73.000084
504 1990-06-04  32.874996  46.749989   74.874962
505 1990-05-29  32.250000  46.499985   74.250000
506 1990-05-21  31.625006  46.874931   68.749916
507 1990-05-14  30.999998  46.374981   66.250084
508 1990-05-07  29.874998  45.874973   61.999916
509 1990-04-30  28.749998  44.249935   56.250000
510 1990-04-23  28.374998  47.624947   58.875118
511 1990-04-16  29.874998  46.624985   60.999840
512 1990-04-09  28.625006  46.624985  113.749916
513 1990-04-02  27.249998  47.124939  109.749596
514 1990-03-26  27.125006  48.749969  110.499832
515 1990-03-19  28.374998  48.374962  113.749916
516 1990-03-12  27.125006  47.124939  106.250404
517 1990-03-05  26.750006  46.874931  103.500000
518 1990-02-26  25.500002  44.624943   97.499519
519 1990-02-20  26.250002  43.999989   97.750084
520 1990-02-12  26.625002  43.999989   94.500000
521 1990-02-05  26.874998  42.749962   93.624481
522 1990-02-01  25.875002  42.999966   92.499832

[523 rows x 4 columns]

In [234]:
from bokeh.charts import Line, output_file, show
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
import warnings

warnings.filterwarnings('ignore')
output_notebook()

pl = Line( fullDataClean.drop(['index'], axis=1), x="Date", title="", legend="top_left", ylabel='Prices')
show(pl)


BokehJS successfully loaded.

ERROR:C:\Users\Home Laptop\Anaconda3\lib\site-packages\bokeh\core\validation\check.py:W-1001 (NO_DATA_RENDERERS): Plot has no data renderers: Figure, ViewModel:Plot, ref _id: 32fe7bf8-e6e9-4861-81df-91d77f62e59a
ERROR:C:\Users\Home Laptop\Anaconda3\lib\site-packages\bokeh\core\validation\check.py:W-1001 (NO_DATA_RENDERERS): Plot has no data renderers: Figure, ViewModel:Plot, ref _id: 20dffe56-35a1-49aa-81a1-2e5229ad5303


NameError: name 'options' is not defined

In [180]:
from ggplot import *
qplot(meat.beef)

ImportError: No module named 'ggplot'